In [1]:
# import neptune.new as neptune
# from neptune.new.types import File

# run = neptune.init(
#     project="arsde/J21-BDT",
#     tags=["xgb", "5M", "MSE", "all features"],
#     run='JBDT-4'
# )

In [2]:
import pandas as pd
import numpy as np
from tqdm.notebook import tqdm

import plotly.graph_objs as go
from plotly.subplots import make_subplots
import plotly.io as pio

from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
import pickle
from tensorflow.keras.models import load_model

import eli5
import shap
from eli5.sklearn import PermutationImportance

import warnings
warnings.filterwarnings("ignore")

In [3]:
train = input()
if train.lower()=='yes':
    train=True
else:
    train=False

no


In [4]:
vm = input()
if vm.lower()=='yes':
    path='/mnt/cephfs/ml_data/mc_2021/'
else:
    path=''

yes


In [5]:
# data_ideal = pd.read_csv('{}processed_data/ProcessedTrainIdeal/ProcessedTrain.csv.gz'.format(path))
# data_ideal = data_ideal[data_ideal['edepR'] < 17.2]

# data_real = pd.read_csv('{}processed_data/ProcessedTrainReal/ProcessedTrain.csv.gz'.format(path))
# data_real = data_real[data_real['edepR'] < 17.2]

In [6]:
# all_data = [data_ideal, data_real]

In [7]:
# from sklearn.model_selection import train_test_split

# X_trains = []
# y_trains = []

# X_vals = []
# y_vals = []

# for i in range(len(all_data)):
#     X = all_data[i].iloc[:, :-5]
#     y = all_data[i].iloc[:, -2]
    
#     X_train, X_val, y_train, y_val = train_test_split(
#         X, y, test_size=0.1, random_state=22)
    
#     X_trains.append(X_train)
#     y_trains.append(y_train)
    
#     X_vals.append(X_val)
#     y_vals.append(y_val)

In [8]:
# from neptune.new.integrations.lightgbm import NeptuneCallback
# from neptune.new.integrations.xgboost import NeptuneCallback
# neptune_callback = NeptuneCallback(run=run)

models = []
if train:
    for i in tqdm(range(len(all_data))):
        model = XGBRegressor(
                max_depth=10,
#                 objective='mape',
                learning_rate=0.08,
                n_estimators=3000,
                random_state=22,
#                 tree_method='gpu_hist'
        )

        model.fit(X_trains[i], y_trains[i], verbose=False,
                   eval_set=[(X_vals[i], y_vals[i])],
                   eval_metric=['rmse'],
#                    callbacks=[neptune_callback],
                   early_stopping_rounds=7)
        
        models.append(model)
        if i == 0:
            option = 'ideal'
        elif i == 1:
            option = 'real'
            
        pickle.dump(model, open("models/xgb_Z_{}_5M_rmse.dat".format(option), "wb"))
#         run['output/model_checkpoints/xgb_energy_{}_5M_rmse.dat'.format(option)].upload(
#             '/home/arsde/J21_SYSU/models/xgb_energy_{}_5M_rmse.dat'.format(option)
#         )

In [9]:
models = []
models.append(pickle.load(open("models/xgb_Z_ideal_5M_rmse.dat", "rb")))
models.append(pickle.load(open("models/xgb_Z_real_5M_rmse.dat", "rb")))
models.append(load_model("models/5M_ideal_Z.h5"))
models.append(load_model("models/5M_real_Z.h5"))

scalers = []
scalers.append(pickle.load(open('models/scaler_ideal_Z.pkl','rb')))
scalers.append(pickle.load(open('models/scaler_real_Z.pkl','rb')))

In [10]:
# models = []
# perms = []

# models.append(pickle.load(open("models/xgb_Z_ideal_5M_rmse.dat", "rb")))
# perms.append(PermutationImportance(models[0], random_state=1).fit(X_vals[0], y_vals[0]))

# models.append(pickle.load(open("models/xgb_Z_real_5M_rmse.dat", "rb")))
# perms.append(PermutationImportance(models[1], random_state=1).fit(X_vals[1], y_vals[1]))

In [11]:
# shap_values = shap.TreeExplainer(models[0]).shap_values(X_vals[0][:5000])
# shap.summary_plot(shap_values, X_vals[0][:5000])

In [12]:
# shap_values = shap.TreeExplainer(models[1]).shap_values(X_vals[1][:5000])
# shap.summary_plot(shap_values, X_vals[1][:5000])

In [13]:
# eli5.show_weights(perms[0], feature_names=X.columns.tolist(), top=15)
# eli5.show_prediction(xgbregs[0], X_vals[0].iloc[100], show_feature_values=True, feature_names=X.columns.tolist())

In [14]:
# eli5.show_weights(perms[1], feature_names=X.columns.tolist(), top=15)

In [15]:
%%time
energies = [0, 0.1, 0.3, 0.6] + list(range(1, 11))
y_true_array = []
y_pred_array = []
for j in tqdm(range(len(models)), "Options..."):
    if j%2==0:
        name = 'ProcessedTestIdeal'
    else:
        name = 'ProcessedTestReal'
    y_true = []
    y_pred = []
    for energy in tqdm(energies, "Energies...", leave=False):
        test = pd.read_csv('{}processed_data/{}/{}MeV.csv.gz'.format(path, name, energy))
        test = test[test['edepR'] < 17.2]
        edepZ = np.array(test['edepZ'])
        if j < len(models)/2:
            X_test = test.iloc[:, :-5]
            edepZ_preds = models[j].predict(X_test)
        else:
            X_test = test.iloc[:, :-5]
            X_test = scalers[j-2].transform(X_test)
            edepZ_preds = models[j].predict(X_test).flatten()

        y_true.append(edepZ)
        y_pred.append(edepZ_preds)
    y_true_array.append(y_true)
    y_pred_array.append(y_pred)

Options...:   0%|          | 0/4 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

Energies...:   0%|          | 0/14 [00:00<?, ?it/s]

CPU times: user 13min 21s, sys: 1min 12s, total: 14min 34s
Wall time: 9min 11s


In [16]:
pio.templates.default = 'plotly_dark'

def plot_predicts(y_pred, y_true, title='', size=10000):
    fig = go.Figure()

    for i in range(len(y_pred)):
        fig.add_trace(
            go.Scattergl(
                x=list(range(y_true[i][:size].shape[0])),
                y=y_pred[i][:size],
                mode='markers',
                opacity=0.75,
                marker=dict(
                    size=3,
                    color='rgb(255, {}, {})'.format(255-i*15, 5*i+10)
                ),
                name='{}MeVXGB'.format(i+1)
            )
        )
        fig.add_trace(
            go.Scattergl(
                x=list(range(y_true[i][:size].shape[0])),
                y=y_true[i][:size],
                mode='markers',
                opacity=0.75,
                marker=dict(
                    size=3,
                    color='rgb(15, {}, {})'.format(100-i*5, 25*i+10)
                ),
                name='{}MeV'.format(i+1)
            )
        )

    fig.update_layout(
        title = title,
        showlegend=False,
        yaxis_title="Energy, MeV",
        xaxis_title="x",
        font=dict(
            family="Times New Roman",
            size=16,
            color="White"
        ),
        xaxis = dict(
            showline=True,
            ticks='outside',
            mirror=True,
            linecolor='black',
            showgrid=True,
            gridcolor='grey',
            gridwidth=0.25,
        ),
        yaxis = dict(
            showline=True,
            ticks='outside',
            mirror=True,
            linecolor='black',
            showgrid=True,
            gridcolor='grey',
            gridwidth=0.25,
            dtick=1,
            zeroline=True,
            zerolinecolor='black',
            zerolinewidth=0.25
            ),
    )

    fig.show()
#     pio.write_image(fig, 'plots/plot_predictions_{}_5M.pdf'.format(title.split(', ')[0]), width=900, height=600)
#     run['output/plot_predictions_{}_5M.pdf'.format(title.split(', ')[0])].upload(File.as_html(fig))

In [17]:
# plot_predicts(y_pred_array[0], y_true_array[0], title='Ideal, 500k')
# plot_predicts(y_pred_array[1], y_true_array[1], title='Real, 5M', size=5000)

In [18]:
diffs = np.array([
    [y_pred_array[j][i] - y_true_array[j][i] for i in range(len(y_pred_array[0]))]
    for j in range(len(y_pred_array))
])

In [19]:
energies = [0, 0.1, 0.3, 0.6] + list(range(1, 11))
energies = np.array([1.022+i for i in energies]).round(5)
energies

array([ 1.022,  1.122,  1.322,  1.622,  2.022,  3.022,  4.022,  5.022,
        6.022,  7.022,  8.022,  9.022, 10.022, 11.022])

In [20]:
names = ['BDT Ideal', 'BDT Real', 'FCDNN Ideal', 'FCDNN Real']

In [21]:
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit
from scipy.stats import norm

a_array = []
errors_array = []
for k in range(diffs.shape[0]):
    a = []
    e = []
    for i in range(diffs.shape[1]):
        fig, ax = plt.subplots()
        nbins = 150
        n, bins, patches = ax.hist(diffs[k][i], nbins, density=True, facecolor = 'grey', alpha = 0.5, label='before');
        plt.close(fig)
        centers = (0.5*(bins[1:]+bins[:-1]))
        pars, cov = curve_fit(lambda x, mu, sig : norm.pdf(x, loc=mu, scale=sig), centers, n, p0=[0,1])  
        a.append(pars)
        e.append(cov)
    a_array.append(a)
    errors_array.append(e)

In [30]:
pio.templates.default = 'plotly_white'

# from scipy import stats
# for k in range(4):
#     fig = go.Figure()

#     for i in range(len(diffs[k])): 
#         x = np.linspace(diffs[k][i][:22500].min(), diffs[k][i][:22500].max(), 100)
#         p = stats.norm.pdf(x, a_array[k][i][0], a_array[k][i][1])

#         fig.add_trace(go.Scattergl(x=x,
#                      y=p, mode='lines', name='mu={:.3f} +- {:.3f}, sigma={:.3f} +- {:.3f}'.format(
#                          a_array[k][i][0], np.sqrt(errors_array[k][i][0][0]),
#                          a_array[k][i][1], np.sqrt(errors_array[k][i][1][1])),
#                         visible = (i==0)
#                     ))

#     for i in range(len(diffs[k])): 
#         fig.add_trace(go.Histogram(x=diffs[k][i][:22500], xbins=dict(size=0.01),
#                       showlegend=False, histnorm='probability density',
#                      visible = (i==0)
#                     ))

#     buttons = []
#     for N in range(0, len(diffs[k])): 
#         buttons.append(
#             dict(
#                  args=['visible', [False]*N + [True] + [False]*(len(diffs[k])-1-N)],
#                      label='Energy =  {} MeV'.format(energies[N]),
#                  method='restyle'
#             )
#         )
        
#     fig.update_layout(

#         xaxis = dict(
#             showline=True,
#             ticks='outside',
#             mirror=True,
#             linecolor='black',
#             showgrid=True,
#             gridcolor='grey',
#             gridwidth=0.25,
#         ),

#         yaxis = dict(
#             showline=True,
#             ticks='outside',
#             mirror=True,
#             linecolor='black',
#             tick0=0,
# #             dtick=1,
#             showgrid=True,
#             gridcolor='grey',
#             gridwidth=0.25,
#             zeroline=True,
#             zerolinecolor='black',
#             zerolinewidth=0.25
#             ),
#     )

#     fig.update_layout(
#         title = '{}'.format(names[k]),
#         xaxis_title=r"$$E_{rec} - E_{true}$$",
#         showlegend=True,
#         updatemenus=list([
#             dict(
#                 x=0.5,
#                 y=1.2,
#                 yanchor='top',
#                 buttons=buttons
#             ),
#         ]),
#         legend=dict(
#             orientation="h",
#             yanchor="bottom",
#             y=1.05,
#             xanchor="right",
#             x=1
#         )
#     )
    
#     fig.show()
# #     run['output/Result_distributions.pdf'].upload(File.as_html(fig))

In [31]:
def plot_results(appr=False):
    
#     y_lin = lambda x: np.sqrt(2.57**2 / x + 0.73**2 + (1.25 / x)**2)
    fig = make_subplots(rows=2, cols=1,
                        shared_xaxes=True,
                        vertical_spacing=0.01,
                        row_width=[0.25, 0.75]
    )

    for k in range(diffs.shape[0]):
        fig.add_trace(
            go.Scatter(
                x=energies,
                y=res[k],
                mode='markers',
                marker=dict(
                    color=colors[k],
                    symbol=symbols[k]
                ),
                showlegend=True,
                error_y=dict(
                    type='data',
                    width=10,
                    array=error_sigma[k],
                    visible=True
                ),
                name=names[k]
            ), row=1, col=1
        )

        fig.add_trace(
            go.Scatter(
                x=energies,
                y=bias[k],
                mode='markers',
                showlegend=False,
                marker=dict(
                    color=colors[k],
                    symbol=symbols[k]
                ),
                error_y=dict(
                        type='data',
                        width=10,
                        array=error_mu[k],
                        visible=True
                ),
                name=names[k]
            ), row=2, col=1
        )

    if appr:
        for k in range(len(names)):
            fig.add_trace(
                go.Scatter(
                    x=x_lin,
                    y=func(x_lin, a[k], b[k], c[k]),
                    mode='lines',
                    line=dict(
                    ),
                    opacity=0.5,
                    showlegend=False,
                    name=names[k],
                    marker=dict(
                        color=colors[k]
                    )
                ), row=1, col=1
            )

    xaxis = dict(
        showline=True,
        ticks='outside',
        mirror=True,
        tick0=1,
        dtick=1,
        linecolor='black',
        showgrid=True,
        gridcolor='grey',
        gridwidth=0.25,
    )

    yaxis = lambda range: dict(
        showline=True,
        ticks='outside',
        mirror=True,
        linecolor='black',
        range=range,
        showgrid=True,
        gridcolor='grey',
        gridwidth=0.25,
        zeroline=True,
        zerolinecolor='black',
        zerolinewidth=0.25
    )

    fig.update_layout(
        xaxis2_title="Visible energy, MeV",
        yaxis1_title="Resolution, mm",
        yaxis2_title="Bias, mm",

        xaxis1 = xaxis,
        xaxis2 = xaxis,
        yaxis1 = yaxis([0, 340]),
        yaxis2 = yaxis([-7.5, 7.5]),

        showlegend=True,
        font=dict(
                family="Times New Roman",
                size=18,
        ),
        legend=dict(
            x=0.75,
            y=0.99,
            title_font_family="Times New Roman",
            font=dict(
                family="Times New Roman",
                size=18,
                color="black"
            ),
            bordercolor="Black",
            borderwidth=2
        )
    )

    fig.show()
    if appr:
        pio.write_image(fig, 'plots/appr_results_5M_Z.pdf', width=900, height=600, scale=1)
#         run['output/appr_results.pdf'].upload(File.as_html(fig))
    else:
        pio.write_image(fig, 'plots/results_5M_Z.pdf', width=900, height=600, scale=1)
#         run['output/results.pdf'].upload(File.as_html(fig))

In [32]:
colors = ['red', 'darkviolet', 'blue', 'green']
symbols = ['hexagon-open', 'star-square', 1, 2]

In [33]:
error_sigma = []
for k in range(diffs.shape[0]):
    error = [1000 * np.sqrt(errors_array[k][i][1][1]) / energies[i] for i in range(len(energies))]
    error_sigma.append(error)
    
error_mu = []
for k in range(diffs.shape[0]):
    error = [1000 * np.sqrt(errors_array[k][i][0][0]) / energies[i] for i in range(len(energies))]
    error_mu.append(error)

In [34]:
res = []
bias = []
for k in range(diffs.shape[0]):
    sigma = [1000 * a_array[k][i][1] / energies[i] for i in range(len(energies))]
    mu = [1000 * a_array[k][i][0] / energies[i] for i in range(len(energies))]
    res.append(sigma)
    bias.append(mu)
    
plot_results()

In [35]:
diff_real = []
z_true_real = []
for i in range(diffs[1].shape[0]):
    diff_real += list(1000*diffs[3][i])
    z_true_real += list(y_true_array[3][i])
    
diff_real = np.array(diff_real)
z_true_real = np.array(z_true_real)

In [36]:
ind = np.random.randint(0, len(diff_real), 50000)

In [37]:
fig = go.Figure(data=go.Histogram2d(x=z_true_real[ind], y=diff_real[ind],
        autobinx=False,
        xbins=dict(size=1),
        autobiny=False,
        ybins=dict(start=-750, end=750, size=40),
        colorscale='balance'))

fig.update_layout(
    xaxis_title="$$z, m$$",
    yaxis_title="$$z_{rec} - z_{true}, mm$$",
    showlegend=True)

fig.show()